# Optimal Energy Storage - Example Usage

This notebook provides some examples of how to use the `optimal-energy-storage` package.

---


## Imports

In [1]:
# Standard libraries
import pandas as pd   # Standard timestamp and dataframe structures
import pickle         # To load example data

# Plotting with plotly
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)

# Local imports
import oes.util.generate_plots as plots
import oes.util.utility as utility

# Enable modules to be autmatically reloaded
%load_ext autoreload
%autoreload 2

---

## Load Example Data

In [2]:
df = pickle.load(open('oes/data/example_data.pickle', 'rb'))

In [3]:
# Let's have a look at structure of this dataframe
df[:5]

generation demand market_price tariff_import  \
timestamp                                                          
2017-11-29 00:00:00          0   1370       114.15           0.2   
2017-11-29 00:01:00          0   1370        91.58           0.2   
2017-11-29 00:02:00          0   1360        91.58           0.2   
2017-11-29 00:03:00          0   1420        91.58           0.2   
2017-11-29 00:04:00          0   1380        91.58           0.2   

                     tariff_export  
timestamp                           
2017-11-29 00:00:00           0.08  
2017-11-29 00:01:00           0.08  
2017-11-29 00:02:00           0.08  
2017-11-29 00:03:00           0.08  
2017-11-29 00:04:00           0.08

In [ ]:
# And let's plot it
iplot(plots.generate_df_fig(df))

In [5]:
# Note that we can also resample to 30-minute resolution if needed
df_30 = utility.convert_resolution(df, pd.Timedelta('30 minutes'))
iplot(plots.generate_df_fig(df_30))

---

## Battery Model

In principle we could develop and use many different types of battery models.  Let's start with a basic one.

In [6]:
from oes import BasicBatteryModel

In [7]:
battery = BasicBatteryModel()

In [8]:
battery.params

{'capacity': 13500,
 'max_charge_rate': 7000,
 'max_discharge_rate': 7000,
 'max_soc': 100,
 'min_soc': 0,
 'current_soc': 50}

## No Battery

As a baseline, run the controller that "does nothing", in other words represents the scenario in which no battery is present.

In [9]:
from oes import DoNothing

In [10]:
controller_dn = DoNothing(params={'time_interval': '1 minute'})
solution_dn = controller_dn.solve(df, battery)
solution_dn = utility.calculate_values_of_interest(df, solution_dn)

In [11]:
iplot(plots.generate_solution_fig(df, solution_dn))

---

## Basic Rule-Based Controllers

### Solar Self-Consumption

In "solar self-consumption", the battery is used to store any excess solar generation.  In other words, it charges when there is more generation than demand, and discharges when there is more demand than generation.

In [12]:
from oes import SolarSelfConsumption

In [13]:
controller_ssc = SolarSelfConsumption(params={'time_interval': '1 minute'})
solution_ssc = controller_ssc.solve(df, battery)
solution_ssc = utility.calculate_values_of_interest(df, solution_ssc)

In [14]:
iplot(plots.generate_solution_fig(df, solution_ssc))

---

### Tariff Optimisation

In "tariff optimisation", the battery is charged when the price for buying electricity is low, and discharges to meet local demand when the price for buying electricity is high.

In [15]:
from oes import TariffOptimisation

In [16]:
controller_to = TariffOptimisation(params={'time_interval': '1 minute'})
solution_to = controller_to.solve(df, battery)
solution_to = utility.calculate_values_of_interest(df, solution_to)

In [17]:
iplot(plots.generate_solution_fig(df, solution_to))

---

### Wholesale Market Participation

In wholesale market participation, the battery discharges to the grid whenever there is a desirable market signal to do so (in other words, whenever the wholesale price (received for exporting) is higher than the price of buying energy (paid for importing).

In [18]:
from oes import MarketParticipation

In [19]:
controller_mp = MarketParticipation(params={'time_interval': '1 minute'})
solution_mp = controller_mp.solve(df, battery)
solution_mp = utility.calculate_values_of_interest(df, solution_mp)

In [20]:
iplot(plots.generate_solution_fig(df, solution_mp))

---

## Optimal Solution Using Dynamic Programming

This solution finds the best possible way to charge/discharge the battery over the horizon using all available value streams.

We'll start by using 30-min resolution data.

In [21]:
from oes import DynamicProgramController

In [22]:
controller_dp = DynamicProgramController(params={'time_interval': '30 minutes',  # Time discretisation
                                                    'soc_interval': 1,  # SOC discretisation (in % SOC)
                                                    'constrain_final_soc': True, # Constrain final SOC
                                                    'final_soc': 50.0, # Reuquested SOC at end of horizon
                                                   })
solution_dp = controller_dp.solve(df_30, battery)
solution_dp = utility.calculate_values_of_interest(df_30, solution_dp)

In [23]:
iplot(plots.generate_solution_fig(df_30, solution_dp))

Let's check if that all works at 1-minute resolution too.  This can take 5-10 minutes to solve.  Optionally, the solution can be loaded from a local file to save time.

In [24]:
# Decide whether to re-run or load from local pickle file
run_full_dp = True

In [25]:
if run_full_dp:
    controller_dp = DynamicProgramController(params={'time_interval': '1 minute',  # Time discretisation
                                                        'soc_interval': 0.1,  # SOC discretisation (in % SOC)
                                                        'constrain_final_soc': True, # Constrain final SOC
                                                        'final_soc': 50.0, # Reuquested SOC at end of horizon
                                                       })
    
    # Let's set debug to True to get some progress updates as we're solving
    controller_dp.debug = True
    
    solution_dp = controller_dp.solve(df, battery)
    solution_dp = utility.calculate_values_of_interest(df, solution_dp)
    
    # Save to local pickle file
    pickle.dump(solution_dp, open('oes/data/result_dp_1min.pickle', 'wb'))

else:
    solution_dp = pickle.load(open('oes/data/result_dp_1min.pickle', 'rb'))

Initialising dynamic program ...
DP grid has size 1001 (num soc intervals) x 1441 (num time intervals)
At each time step, 
 - battery may    charge at most 117Wh, a change in soc of 0.864% (9 intervals)
 - battery may discharge at most 117Wh, a change in soc of -0.864% (-9 intervals)
Running dynamic program ...
  0% ...
 10% ...
 20% ...
 30% ...
 40% ...
 50% ...
 60% ...
 70% ...
 80% ...
 90% ...
 100% ...
Calculating optimal profile ...
Total run time: 1m 34s


In [26]:
iplot(plots.generate_solution_fig(df, solution_dp))

---

## Economic Evaluation

Let's have a quick look at how the different algorithms stack up against one another in terms of accumulated cost throughout the day.

In [27]:
solutions = {
   'none': solution_dn,
    'ssc': solution_ssc, 
     'to': solution_to, 
     'mp': solution_mp, 
     'dp': solution_dp
}

In [28]:
evaluation = utility.compare_solutions(solutions)

In [29]:
iplot(plots.generate_evaluation_fig(evaluation))


---

## Scheduling

Ok, now we get to a very interesting part.  How can a solution such as the dynamic program above, which calculates charge and discharge rates in discrete intervals, be turned into a schedule of simple controllers?

A key building block is that we can represent some very simple battery behaviours (nothing, charge, discharge) as "controllers".  Doing nothing corresponds to not having a battery (see top of this notebook).

We can then explore the behaviours of `do_nothing`, `charge`, `discharge`, `solar_self_consumption`, `tariff_optimisation`, and `market_participation`, ... and compare them to the output of the optimal `dynamic_program`.  A key thing here is to ensure that each controller is "stateless", in other words we set `constrain_charge_rate = False`.

In [30]:
from oes import DPScheduler
scheduler = DPScheduler(
    params = {
        'threshold_near_optimal': 600,
        'resample_length': '30 minutes',
    }
)

In [31]:
# Generate list of controllers to use when generating schedule

from oes import DoNothing, Charge, Discharge, SolarSelfConsumption, TariffOptimisation, MarketParticipation

controllers = {
    'DN':  DoNothing,
    'C':   Charge,
    'D':   Discharge,
    'SSC': SolarSelfConsumption,
    'TO':  TariffOptimisation,
    'MP':  MarketParticipation
}

In [32]:
scheduler.solve(df, battery, controllers, solution_dp)

Finding solution for DN ...
Finding solution for C ...
Finding solution for D ...
Finding solution for SSC ...
Finding solution for TO ...
Finding solution for MP ...
Generating initial full schedule ...
Complete.


Let's first compare the charge rates for each controller:

In [33]:
iplot(plots.generate_schedule_charge_rate_fig(scheduler.charge_rates))

Next, let's see which charge rates match the optimal dynamic program most closely:

In [34]:
scheduler.charge_rates[:10]

DN     C     D   SSC    TO    MP      DP
timestamp                                                    
2017-11-29 00:00:00   0     0     0 -1370  7000  7000  7290.0
2017-11-29 00:01:00   0  7000 -7000 -1370  7000  7000  7290.0
2017-11-29 00:02:00   0  7000 -7000 -1360  7000  7000  7290.0
2017-11-29 00:03:00   0  7000 -7000 -1420  7000  7000  7290.0
2017-11-29 00:04:00   0  7000 -7000 -1380  7000  7000  7290.0
2017-11-29 00:05:00   0  7000 -7000 -1340  7000  7000  7290.0
2017-11-29 00:06:00   0  7000 -7000 -1340  7000  7000  7290.0
2017-11-29 00:07:00   0  7000 -7000 -1330  7000  7000  7290.0
2017-11-29 00:08:00   0  7000 -7000 -1330  7000  7000  7290.0
2017-11-29 00:09:00   0  7000 -7000 -1340  7000  7000  7290.0

In [35]:
scheduler.near_optimal[:10]

DN  C  D  SSC  TO  MP  DP
timestamp                                     
2017-11-29 00:00:00   0  0  0    0   1   1   1
2017-11-29 00:01:00   0  1  0    0   1   1   1
2017-11-29 00:02:00   0  1  0    0   1   1   1
2017-11-29 00:03:00   0  1  0    0   1   1   1
2017-11-29 00:04:00   0  1  0    0   1   1   1
2017-11-29 00:05:00   0  1  0    0   1   1   1
2017-11-29 00:06:00   0  1  0    0   1   1   1
2017-11-29 00:07:00   0  1  0    0   1   1   1
2017-11-29 00:08:00   0  1  0    0   1   1   1
2017-11-29 00:09:00   0  1  0    0   1   1   1

In [36]:
scheduler.near_optimal_clean[:10]

DN  C  D  SSC  TO  MP  DP
timestamp                                     
2017-11-29 00:00:00   0  0  0    0   1   1   1
2017-11-29 00:01:00   0  1  0    0   1   1   1
2017-11-29 00:02:00   0  1  0    0   1   1   1
2017-11-29 00:03:00   0  1  0    0   1   1   1
2017-11-29 00:04:00   0  1  0    0   1   1   1
2017-11-29 00:05:00   0  1  0    0   1   1   1
2017-11-29 00:06:00   0  1  0    0   1   1   1
2017-11-29 00:07:00   0  1  0    0   1   1   1
2017-11-29 00:08:00   0  1  0    0   1   1   1
2017-11-29 00:09:00   0  1  0    0   1   1   1

In [37]:
iplot(plots.generate_schedule_near_optimal_fig(scheduler.near_optimal))

In [38]:
# Let's have a look at cleaned version
iplot(plots.generate_schedule_near_optimal_fig(scheduler.near_optimal_clean))

In [39]:
scheduler.short_schedule

controller
timestamp                     
2017-11-29 00:00:00         TO
2017-11-29 00:01:00          C
2017-11-29 00:55:00         DN
2017-11-29 00:58:00        SSC
2017-11-29 01:13:00         DN
2017-11-29 01:24:00        SSC
2017-11-29 01:29:00         DN
2017-11-29 01:34:00        SSC
2017-11-29 01:39:00         DN
2017-11-29 01:56:00        SSC
2017-11-29 03:25:00         DN
2017-11-29 03:30:00        SSC
2017-11-29 03:51:00         DN
2017-11-29 04:04:00        SSC
2017-11-29 04:20:00         DN
2017-11-29 04:24:00        SSC
2017-11-29 04:32:00         DN
2017-11-29 04:34:00        SSC
2017-11-29 04:35:00         DN
2017-11-29 04:37:00        SSC
2017-11-29 14:00:00          D
2017-11-29 14:01:00         TO
2017-11-29 14:02:00        SSC
2017-11-29 16:30:00         MP
2017-11-29 17:31:00        SSC
2017-11-29 19:05:00         TO
2017-11-29 23:00:00          C
2017-11-29 23:56:00        SSC

Ok great, there you have it.  An optimal discrete solution converted into a schedule for simple rule-based controllers.

There is certainly more work to be done, and this could likely be converted into a much simpler schedule still, but this is just a start for now.